In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/credential/Reddit credential.txt


# Reddit

In [2]:
import requests
import json
from IPython.display import JSON
from datetime import datetime

In [3]:
with open("/kaggle/input/credential/Reddit credential.txt", "r") as f:
    file = f.read()
file = file.split()

In [4]:
Client_ID = file[0]
Secret_key = file[1]
User_name = file[2]
Password = file[3]

In [5]:
auth = requests.auth.HTTPBasicAuth(Client_ID, Secret_key)

data = {
    "grant_type": "password",
    "username": User_name,
    "password": Password
}

headers = {"User-Agent": "MyAPI/0.0.1"}

res = requests.post("https://www.reddit.com/api/v1/access_token", auth=auth, data=data, headers=headers)

TOKEN = res.json()["access_token"]

headers["Authorization"] = f"bearer {TOKEN}"
#headers

In [6]:
# Subreddit posts
subreddit="StockMarket"
get_method="hot"
params={"limit":100,
        "threaded":True,
        "sort":"new"
       }
request= requests.get(f"https://oauth.reddit.com/r/{subreddit}/{get_method}", headers=headers, params=params)
request= request.json()
JSON(request)

<IPython.core.display.JSON object>

In [7]:
pd.json_normalize(request["data"]["children"],
                  #record_path=[""],
                  #meta=[""],
                  max_level=1)[["data.name", "data.link_flair_css_class", "data.upvote_ratio", "data.total_awards_received", "data.num_comments", "data.score", "data.title"]]

data.name data.link_flair_css_class  data.upvote_ratio  \
0    t3_1bsyq77                discussion               0.86   
1    t3_1d0xc1j                discussion               0.67   
2    t3_1d15bpk                discussion               0.75   
3    t3_1d1dxex                discussion               0.65   
4    t3_1d0nsg7           flair-valuation               0.94   
..          ...                       ...                ...   
97   t3_1ct8jwk                discussion               0.79   
98   t3_1ctxi6k                discussion               0.30   
99   t3_1ctcs5v                discussion               0.50   
100  t3_1cszed4                      news               0.80   
101  t3_1ctj8g4                discussion               0.41   

     data.total_awards_received  data.num_comments  data.score  \
0                             0                109          18   
1                             0                 11           1   
2                             0                108          66   
3                             0                 11           7   
4                             0                 17         286   
..                          ...                ...         ...   
97                            0                  6          10   
98                            0                  2           0   
99                            0                 14           0   
100                           0                  2          14   
101                           0                 17           0   

                                            data.title  
0    Rate My Portfolio - r/StockMarket Quarterly Th...  
1    Daily General Discussion and Advice Thread - M...  
2        Are You Proud of the Companies You Invest In?  
3                       About 401k investment break up  
4    Nvidia Goes Solo: Too Big to Mingle in the SMH...  
..                                                 ...  
97   Daily General Discussion and Advice Thread - M...  
98   Does anyone know why trading balance is low th...  
99         These are the stocks on my watchlist (5/16)  
100  3M’s stock surges to 16-month high after divid...  
101      Looking for some help on my current position.  

[102 rows x 7 columns]

In [8]:
all_data = []
for children in request["data"]["children"]:
    data={"name": children["data"]["name"],
          "css_class": children["data"]["link_flair_css_class"],
          "upvote_ratio": children["data"]["upvote_ratio"],
          #"post_hint": children["data"]["post_hint"],
          "awards": children["data"]["total_awards_received"],
          "num_comments": children["data"]["num_comments"],
          "score": children["data"]["score"],
          "title": children["data"]["title"]}
    all_data.append(data)
df = pd.DataFrame(all_data)
df

name        css_class  upvote_ratio  awards  num_comments  score  \
0    t3_1bsyq77       discussion          0.86       0           109     18   
1    t3_1d0xc1j       discussion          0.67       0            11      1   
2    t3_1d15bpk       discussion          0.75       0           108     66   
3    t3_1d1dxex       discussion          0.65       0            11      7   
4    t3_1d0nsg7  flair-valuation          0.94       0            17    286   
..          ...              ...           ...     ...           ...    ...   
97   t3_1ct8jwk       discussion          0.79       0             6     10   
98   t3_1ctxi6k       discussion          0.30       0             2      0   
99   t3_1ctcs5v       discussion          0.50       0            14      0   
100  t3_1cszed4             news          0.80       0             2     14   
101  t3_1ctj8g4       discussion          0.41       0            17      0   

                                                 title  
0    Rate My Portfolio - r/StockMarket Quarterly Th...  
1    Daily General Discussion and Advice Thread - M...  
2        Are You Proud of the Companies You Invest In?  
3                       About 401k investment break up  
4    Nvidia Goes Solo: Too Big to Mingle in the SMH...  
..                                                 ...  
97   Daily General Discussion and Advice Thread - M...  
98   Does anyone know why trading balance is low th...  
99         These are the stocks on my watchlist (5/16)  
100  3M’s stock surges to 16-month high after divid...  
101      Looking for some help on my current position.  

[102 rows x 7 columns]

In [9]:
# /search
params={
        "limit": 100,
        "type": "sr",
        #"t": "all",
        "q": "Taiwan"
       }
request= requests.get(f"https://oauth.reddit.com/search", headers=headers, params=params)
request= request.json()
JSON(request)

<IPython.core.display.JSON object>

In [10]:
# Subreddit posts
subreddit="StockMarket"
get_method="hot"
params={"limit":100,
        "threaded":True,
        "sort":"new"
       }
request= requests.get(f"https://oauth.reddit.com/r/{subreddit}/{get_method}", headers=headers, params=params)
request= request.json()
JSON(request)

<IPython.core.display.JSON object>

In [11]:
pd.json_normalize(request["data"]["children"],
                  #record_path=[""],
                  #meta=[""],
                  max_level=1)[["data.name", "data.link_flair_css_class", "data.upvote_ratio", "data.total_awards_received", "data.num_comments", "data.score", "data.title"]]

data.name data.link_flair_css_class  data.upvote_ratio  \
0    t3_1bsyq77                discussion               0.83   
1    t3_1d0xc1j                discussion               0.67   
2    t3_1d15bpk                discussion               0.75   
3    t3_1d1dxex                discussion               0.65   
4    t3_1d0nsg7           flair-valuation               0.94   
..          ...                       ...                ...   
97   t3_1ct8jwk                discussion               0.89   
98   t3_1ctxi6k                discussion               0.27   
99   t3_1ctcs5v                discussion               0.54   
100  t3_1cszed4                      news               0.75   
101  t3_1ctj8g4                discussion               0.38   

     data.total_awards_received  data.num_comments  data.score  \
0                             0                109          17   
1                             0                 11           1   
2                             0                108          66   
3                             0                 11           7   
4                             0                 17         286   
..                          ...                ...         ...   
97                            0                  6          14   
98                            0                  2           0   
99                            0                 14           2   
100                           0                  2          11   
101                           0                 17           0   

                                            data.title  
0    Rate My Portfolio - r/StockMarket Quarterly Th...  
1    Daily General Discussion and Advice Thread - M...  
2        Are You Proud of the Companies You Invest In?  
3                       About 401k investment break up  
4    Nvidia Goes Solo: Too Big to Mingle in the SMH...  
..                                                 ...  
97   Daily General Discussion and Advice Thread - M...  
98   Does anyone know why trading balance is low th...  
99         These are the stocks on my watchlist (5/16)  
100  3M’s stock surges to 16-month high after divid...  
101      Looking for some help on my current position.  

[102 rows x 7 columns]

In [12]:
def queryDataFrame(request):
    query = pd.json_normalize(request["data"]["children"],
                              max_level=1)[["data.name", "data.subreddit", "data.created_utc", "data.title", "data.num_comments", "data.link_flair_css_class", "data.upvote_ratio", "data.total_awards_received",  "data.score"]]
    return query 

query = queryDataFrame(request)
query

data.name data.subreddit  data.created_utc  \
0    t3_1bsyq77    StockMarket      1.711962e+09   
1    t3_1d0xc1j    StockMarket      1.716714e+09   
2    t3_1d15bpk    StockMarket      1.716741e+09   
3    t3_1d1dxex    StockMarket      1.716766e+09   
4    t3_1d0nsg7    StockMarket      1.716678e+09   
..          ...            ...               ...   
97   t3_1ct8jwk    StockMarket      1.715850e+09   
98   t3_1ctxi6k    StockMarket      1.715923e+09   
99   t3_1ctcs5v    StockMarket      1.715866e+09   
100  t3_1cszed4    StockMarket      1.715817e+09   
101  t3_1ctj8g4    StockMarket      1.715882e+09   

                                            data.title  data.num_comments  \
0    Rate My Portfolio - r/StockMarket Quarterly Th...                109   
1    Daily General Discussion and Advice Thread - M...                 11   
2        Are You Proud of the Companies You Invest In?                108   
3                       About 401k investment break up                 11   
4    Nvidia Goes Solo: Too Big to Mingle in the SMH...                 17   
..                                                 ...                ...   
97   Daily General Discussion and Advice Thread - M...                  6   
98   Does anyone know why trading balance is low th...                  2   
99         These are the stocks on my watchlist (5/16)                 14   
100  3M’s stock surges to 16-month high after divid...                  2   
101      Looking for some help on my current position.                 17   

    data.link_flair_css_class  data.upvote_ratio  data.total_awards_received  \
0                  discussion               0.83                           0   
1                  discussion               0.67                           0   
2                  discussion               0.75                           0   
3                  discussion               0.65                           0   
4             flair-valuation               0.94                           0   
..                        ...                ...                         ...   
97                 discussion               0.89                           0   
98                 discussion               0.27                           0   
99                 discussion               0.54                           0   
100                      news               0.75                           0   
101                discussion               0.38                           0   

     data.score  
0            17  
1             1  
2            66  
3             7  
4           286  
..          ...  
97           14  
98            0  
99            2  
100          11  
101           0  

[102 rows x 9 columns]

In [13]:
query["data.created_utc"] = pd.to_datetime(query["data.created_utc"],unit='s')
query

data.name data.subreddit    data.created_utc  \
0    t3_1bsyq77    StockMarket 2024-04-01 09:01:55   
1    t3_1d0xc1j    StockMarket 2024-05-26 09:00:56   
2    t3_1d15bpk    StockMarket 2024-05-26 16:37:55   
3    t3_1d1dxex    StockMarket 2024-05-26 23:18:23   
4    t3_1d0nsg7    StockMarket 2024-05-25 22:55:46   
..          ...            ...                 ...   
97   t3_1ct8jwk    StockMarket 2024-05-16 09:00:57   
98   t3_1ctxi6k    StockMarket 2024-05-17 05:18:45   
99   t3_1ctcs5v    StockMarket 2024-05-16 13:22:12   
100  t3_1cszed4    StockMarket 2024-05-15 23:47:47   
101  t3_1ctj8g4    StockMarket 2024-05-16 18:00:23   

                                            data.title  data.num_comments  \
0    Rate My Portfolio - r/StockMarket Quarterly Th...                109   
1    Daily General Discussion and Advice Thread - M...                 11   
2        Are You Proud of the Companies You Invest In?                108   
3                       About 401k investment break up                 11   
4    Nvidia Goes Solo: Too Big to Mingle in the SMH...                 17   
..                                                 ...                ...   
97   Daily General Discussion and Advice Thread - M...                  6   
98   Does anyone know why trading balance is low th...                  2   
99         These are the stocks on my watchlist (5/16)                 14   
100  3M’s stock surges to 16-month high after divid...                  2   
101      Looking for some help on my current position.                 17   

    data.link_flair_css_class  data.upvote_ratio  data.total_awards_received  \
0                  discussion               0.83                           0   
1                  discussion               0.67                           0   
2                  discussion               0.75                           0   
3                  discussion               0.65                           0   
4             flair-valuation               0.94                           0   
..                        ...                ...                         ...   
97                 discussion               0.89                           0   
98                 discussion               0.27                           0   
99                 discussion               0.54                           0   
100                      news               0.75                           0   
101                discussion               0.38                           0   

     data.score  
0            17  
1             1  
2            66  
3             7  
4           286  
..          ...  
97           14  
98            0  
99            2  
100          11  
101           0  

[102 rows x 9 columns]

In [14]:
def intesiveSearch(query, pagesNum):
    # First page inquery
    params={
            "limit": 100,
            #"t": "year", #"all"
            "q": query
           }
    request= requests.get(f"https://oauth.reddit.com/search", headers=headers, params=params)
    request= request.json()
    
    # query dataFrame generation
    page = queryDataFrame(request)
    
    #get last row. It will be our index for the next page.
    index = page["data.name"].tail(1)
    
    for i in range(pagesNum - 1):
        params={
                "limit": 100,
                #"t": "year",
                "after": index,
                "q": query
               }
        request= requests.get(f"https://oauth.reddit.com/search", headers=headers, params=params)
        request= request.json()
        #print(request["data"]['dist'])
        
        if request["data"]['dist'] == 0:
            break
        
        newPage = queryDataFrame(request)
        page = pd.concat([page, newPage])
        index = page["data.name"].tail(1)
        
    return page

In [15]:
query = intesiveSearch("taiwan usa", 4)
query

data.name         data.subreddit  data.created_utc  \
0   t3_12kjmow              worldnews      1.681380e+09   
1   t3_17s7w2w             ChinaWarns      1.699634e+09   
2    t3_rtwu6b            geopolitics      1.641083e+09   
3   t3_1b7ac6p               IWantOut      1.709658e+09   
4   t3_1cx5qn6      explainlikeimfive      1.716291e+09   
..         ...                    ...               ...   
23  t3_16qs1sl            yakuzagames      1.695543e+09   
24   t3_xhj3q4                 taiwan      1.663514e+09   
25   t3_ycuzif                Aupairs      1.666669e+09   
26   t3_gr739i  StreetviewCarSpotting      1.590532e+09   
27  t3_15ex257                 taiwan      1.690850e+09   

                                           data.title  data.num_comments  \
0   Macron on Taiwan: 'An ally not a vassal of USA...               1640   
1   China warns the sovereign nation USA not to re...                358   
2    Is defending Taiwan the best option for the USA?                567   
3               [IWantOut] 31M Taiwan/USA-&gt; Canada                 17   
4   ELI5: Why does China and USA want Taiwan so much?                141   
..                                                ...                ...   
23  yakuza main characters and which country i thi...                132   
24         How do I mail a letter from Taiwan to USA?                  8   
25                  Rec us Agency: HF USA / AP Taiwan                  2   
26          Taiwan, USA, Netherlands and a few others                  1   
27  Which flag should I use when representing Taiwan?                250   

   data.link_flair_css_class  data.upvote_ratio  data.total_awards_received  \
0                       None               0.91                           0   
1                       None               0.92                           0   
2                 discussion               0.77                           0   
3                       None               0.44                           0   
4                      Other               0.36                           0   
..                       ...                ...                         ...   
23                                         0.94                           0   
24                  offtopic               0.75                           0   
25                                         1.00                           0   
26                      None               1.00                           0   
27                discussion               0.70                           0   

    data.score  
0         5513  
1          927  
2          384  
3            0  
4            0  
..         ...  
23         487  
24           8  
25           2  
26           5  
27          53  

[228 rows x 9 columns]

In [16]:
params={
        "limit": 100,
        #"t": "all",
        "after": "t3_12ckluo",
        "q": "Taiwan"
       }
request= requests.get(f"https://oauth.reddit.com/search", headers=headers, params=params)
request= request.json()
JSON(request)

<IPython.core.display.JSON object>

In [17]:
query["data.created_utc"] = pd.to_datetime(query["data.created_utc"],unit='s')
query

data.name         data.subreddit    data.created_utc  \
0   t3_12kjmow              worldnews 2023-04-13 10:05:30   
1   t3_17s7w2w             ChinaWarns 2023-11-10 16:36:02   
2    t3_rtwu6b            geopolitics 2022-01-02 00:28:10   
3   t3_1b7ac6p               IWantOut 2024-03-05 17:02:05   
4   t3_1cx5qn6      explainlikeimfive 2024-05-21 11:38:05   
..         ...                    ...                 ...   
23  t3_16qs1sl            yakuzagames 2023-09-24 08:07:57   
24   t3_xhj3q4                 taiwan 2022-09-18 15:07:32   
25   t3_ycuzif                Aupairs 2022-10-25 03:42:06   
26   t3_gr739i  StreetviewCarSpotting 2020-05-26 22:25:04   
27  t3_15ex257                 taiwan 2023-08-01 00:29:25   

                                           data.title  data.num_comments  \
0   Macron on Taiwan: 'An ally not a vassal of USA...               1640   
1   China warns the sovereign nation USA not to re...                358   
2    Is defending Taiwan the best option for the USA?                567   
3               [IWantOut] 31M Taiwan/USA-&gt; Canada                 17   
4   ELI5: Why does China and USA want Taiwan so much?                141   
..                                                ...                ...   
23  yakuza main characters and which country i thi...                132   
24         How do I mail a letter from Taiwan to USA?                  8   
25                  Rec us Agency: HF USA / AP Taiwan                  2   
26          Taiwan, USA, Netherlands and a few others                  1   
27  Which flag should I use when representing Taiwan?                250   

   data.link_flair_css_class  data.upvote_ratio  data.total_awards_received  \
0                       None               0.91                           0   
1                       None               0.92                           0   
2                 discussion               0.77                           0   
3                       None               0.44                           0   
4                      Other               0.36                           0   
..                       ...                ...                         ...   
23                                         0.94                           0   
24                  offtopic               0.75                           0   
25                                         1.00                           0   
26                      None               1.00                           0   
27                discussion               0.70                           0   

    data.score  
0         5513  
1          927  
2          384  
3            0  
4            0  
..         ...  
23         487  
24           8  
25           2  
26           5  
27          53  

[228 rows x 9 columns]

In [18]:
query.describe()

data.created_utc  data.num_comments  data.upvote_ratio  \
count                            228         228.000000         228.000000   
mean   2023-02-21 23:50:09.780701696          54.771930           0.847763   
min              2015-11-15 05:35:44           0.000000           0.170000   
25%    2022-08-10 18:51:05.249999872           1.000000           0.750000   
50%              2023-06-19 18:44:48          11.000000           0.935000   
75%       2023-11-19 06:22:16.500000          44.250000           1.000000   
max              2024-05-25 00:51:46        1640.000000           1.000000   
std                              NaN         142.187909           0.198012   

       data.total_awards_received   data.score  
count                       228.0   228.000000  
mean                          0.0   191.350877  
min                           0.0     0.000000  
25%                           0.0     1.000000  
50%                           0.0     5.000000  
75%                           0.0    56.500000  
max                           0.0  5513.000000  
std                           0.0   610.031089

In [19]:
query["data.created_utc"].min()

Timestamp('2015-11-15 05:35:44')

In [20]:
query[query.duplicated(['data.name'], keep=False)]

Empty DataFrame
Columns: [data.name, data.subreddit, data.created_utc, data.title, data.num_comments, data.link_flair_css_class, data.upvote_ratio, data.total_awards_received, data.score]
Index: []

In [21]:
query["data.created_utc"].unique()

<DatetimeArray>
['2023-04-13 10:05:30', '2023-11-10 16:36:02', '2022-01-02 00:28:10',
 '2024-03-05 17:02:05', '2024-05-21 11:38:05', '2023-11-11 01:27:46',
 '2022-10-27 02:02:25', '2022-09-19 03:23:00', '2023-04-09 12:12:27',
 '2024-05-24 06:06:40',
 ...
 '2023-06-13 06:03:57', '2021-12-19 18:21:23', '2023-03-29 18:47:23',
 '2023-09-13 21:21:47', '2023-07-06 12:58:48', '2023-09-24 08:07:57',
 '2022-09-18 15:07:32', '2022-10-25 03:42:06', '2020-05-26 22:25:04',
 '2023-08-01 00:29:25']
Length: 228, dtype: datetime64[ns]

In [22]:
# [/r/subreddit]/comments/article
postId= "128l6rd"#df.loc[df["num_comments"].idxmax()]["name"]#all_data[4]["name"][3:]
params={#"limit":10000,
        #"threaded":True,
        #"sort":"new"
       }
request = requests.get(f"https://oauth.reddit.com/comments/{postId}", headers=headers)
request = request.json()
JSON(request)

<IPython.core.display.JSON object>

In [23]:
#Post More comments
postId= df.loc[df["num_comments"].idxmax()]["name"]
link_id = "t3_128l6rd"#postId#f"t3_{postId}" t3_128l6rd
children = "jej8wi6,jej8osr"
params={"api_type": "json",
        "link_id":link_id,
        "children":children,
        "sort":"new"
       }
requestMore = requests.get("https://oauth.reddit.com/api/morechildren", headers=headers, params=params)
requestMore = requestMore.json()
JSON(requestMore)

<IPython.core.display.JSON object>

In [24]:
postId

't3_1d02ppc'

In [25]:
requestMore = requests.get(f"http://oauth.reddit.com/api/morechildren?link_id={link_id}&children={children}&api_type=json", headers=headers)
requestMore = requestMore.json()
JSON(requestMore)

<IPython.core.display.JSON object>

In [26]:
#json.loads(request.text)
#pd.read_json(request)
#pd.DataFrame.from_dict(request, orient='index')
pd.json_normalize(request,
                  record_path=["data", "children"],
                  max_level=1)[["data.replies", "data.body"]]#.loc[[3]]

data.replies  \
0                                                 NaN   
1   {'kind': 'Listing', 'data': {'after': None, 'd...   
2   {'kind': 'Listing', 'data': {'after': None, 'd...   
3   {'kind': 'Listing', 'data': {'after': None, 'd...   
4   {'kind': 'Listing', 'data': {'after': None, 'd...   
5   {'kind': 'Listing', 'data': {'after': None, 'd...   
6   {'kind': 'Listing', 'data': {'after': None, 'd...   
7                                                       
8   {'kind': 'Listing', 'data': {'after': None, 'd...   
9   {'kind': 'Listing', 'data': {'after': None, 'd...   
10  {'kind': 'Listing', 'data': {'after': None, 'd...   
11  {'kind': 'Listing', 'data': {'after': None, 'd...   
12  {'kind': 'Listing', 'data': {'after': None, 'd...   
13                                                      
14  {'kind': 'Listing', 'data': {'after': None, 'd...   
15                                                      
16                                                      
17  {'kind': 'Listing', 'data': {'after': None, 'd...   
18  {'kind': 'Listing', 'data': {'after': None, 'd...   
19  {'kind': 'Listing', 'data': {'after': None, 'd...   
20  {'kind': 'Listing', 'data': {'after': None, 'd...   
21                                                      
22  {'kind': 'Listing', 'data': {'after': None, 'd...   
23  {'kind': 'Listing', 'data': {'after': None, 'd...   
24                                                      
25  {'kind': 'Listing', 'data': {'after': None, 'd...   
26                                                      
27                                                      
28                                                      
29                                                      
30                                                      
31                                                      
32  {'kind': 'Listing', 'data': {'after': None, 'd...   
33                                                      
34                                                      
35                                                      
36                                                      
37                                                      
38  {'kind': 'Listing', 'data': {'after': None, 'd...   
39                                                      
40                                                      
41                                                      
42                                                      
43                                                      
44                                                      
45  {'kind': 'Listing', 'data': {'after': None, 'd...   
46                                                      
47                                                      
48                                                      
49                                                      
50                                                      
51                                                      
52                                                      
53                                                      
54                                                      
55                                                      
56  {'kind': 'Listing', 'data': {'after': None, 'd...   
57                                                      
58                                                NaN   

                                            data.body  
0                                                 NaN  
1   “There’s a housing shortage!”\n\n“There’s too ...  
2                      I'll believe it when I see it.  
3   Basically all the charts regarding mortgages c...  
4   Architect here, multifamily projects and Healt...  
5   I’m sorry but this needs to be said….good. \n\...  
6         About time normal people got some good news  
7   This is also interesting for the whole return ...  
8          Hahaha...this dude thinks rent goes lower.  
9   Good. 70% of Americans 41 years of age and you...  
10  

In [27]:
def replies_data(children, thread):
    data={"name": children["data"]["name"],
          "thread": thread,
          "comment": children["data"]["body"],
          "reply": True,
          "score": children["data"]["score"]
         }
    #print(children["data"]["body"])
    return data

def comment_data(children, thread):
    data={"name": children["data"]["name"],
          "thread": thread,
          "comment": children["data"]["body"],
          "reply": False,
          "score": children["data"]["score"]
         }
    #print(children["data"]["body"])
    return data

def collect_more(link_id, children_links, all_data, thread, replyCount):
    for children_link in children_links:
        requestMore = requests.get(f"http://oauth.reddit.com/api/morechildren?link_id={link_id}&children={children_link}&api_type=json", headers=headers)
        requestMore = requestMore.json()
        #print(requestMore)
        for moreChildren in requestMore["json"]["data"]["things"]:
            if moreChildren["data"]["name"] != "t1__":
                if moreChildren["data"]["replies"] == "":
                    if replyCount == None:
                        all_data.append(comment_data(moreChildren, thread))
                        thread+=1
                    else:
                        all_data.append(replies_data(moreChildren, f"{thread}.{replyCount}"))
                        #print(f"{thread}.{replyCount}")
                        replyCount+=1
                else:
                    all_data.append(replies_data(moreChildren, f"{thread}.{replyCount}"))

                    repliesCursor = moreChildren["data"]["replies"]

                    collect_all_replies(repliesCursor, all_data, f"{thread}.{replyCount}")
            #else:
                #print("Empty moreChild :", moreChildren["data"]["children"])
        
def collect_all_replies(repliesCursor, all_data, thread):
    #Collect all replies of each comments
    replyCount=0
    for children in repliesCursor["data"]["children"]:
        #If the comment is not a moreChildren list
        if children["kind"] != "more":
            data = replies_data(children, f"{thread}.{replyCount}")
            #print(f"{thread}.{replyCount}")
            #print(children["data"]["body"])
            repliesCursor = children["data"]["replies"]
            
            #If there is replies to this comment
            if repliesCursor != "":
                collect_all_replies(repliesCursor , all_data, f"{thread}.{replyCount}")

            replyCount+=1
            all_data.append(data)
        else:
            #link_id = postId
            children_links = children["data"]["children"]
            #print(link_id, children_links)
            
            collect_more(link_id, children_links, all_data, thread, replyCount)

In [28]:
parent_id = ""
children_links = ""
all_data = []
ComCount = 0
    
for first_children in request[1]["data"]["children"]:
    
    if first_children["kind"] != "more" and first_children["data"]["replies"] == "":
        all_data.append(comment_data(first_children, ComCount))
        
    elif first_children["kind"] != "more" and first_children["data"]["replies"] != "":
        all_data.append(replies_data(first_children, ComCount))
        
        repliesCursor = first_children["data"]["replies"]
        
        collect_all_replies(repliesCursor, all_data, ComCount)
        
    else:
        #parent_id = first_children["data"]["parent_id"]
        children_links = first_children["data"]["children"]
        #print(children_links)
        collect_more(link_id, children_links, all_data, ComCount, None)
 
            
        
    ComCount+=1
    #if first_children["data"]["replies"] not null 
    #print(first_children["data"]["replies"])
    
dfCom = pd.DataFrame(all_data)
dfCom

name           thread  \
0    t1_jejbve6                0   
1    t1_jenxvwq  0.0.0.0.0.0.0.0   
2    t1_jemxr25  0.0.0.0.0.0.0.1   
3    t1_jel6f96    0.0.0.0.0.0.0   
4    t1_jenxm3e    0.0.0.0.0.0.1   
..          ...              ...   
897  t1_jeoazbd              356   
898  t1_jel3ujj              357   
899  t1_jel3zb2              358   
900  t1_jjqeyc8              359   
901  t1_jel69sb              360   

                                               comment  reply  score  
0    “There’s a housing shortage!”\n\n“There’s too ...   True    833  
1    If it has to have an LA address, what I found ...   True      4  
2                          And that’s if you’re lucky!   True      1  
3        And 400K might get you a tiny 1 bedroom condo   True     12  
4                         That's absolutely obnoxious.   True      2  
..                                                 ...    ...    ...  
897  I think it’s the moving back in with parents c...  False      1  
898  Jeez, come to the midwest. I’m just south of K...  False      1  
899                                       Yeah. Right.  False      1  
900                      Lol “lower rents”. Yeah right  False      1  
901  Not really. It might bring prices down and inv...  False      1  

[902 rows x 5 columns]

In [29]:
dfCom[dfCom.duplicated(['comment'], keep=False)]

name           thread  \
16   t1_jelvzyl    0.0.0.0.1.0.5   
21   t1_jemm5z2   0.0.0.0.1.0.10   
36   t1_jem291h        0.0.0.0.3   
67   t1_jenzc77  0.0.0.1.1.0.0.2   
69   t1_jel6u60    0.0.0.1.1.0.0   
71   t1_jekyrir        0.0.0.1.1   
145  t1_jejwow6             0.10   
146  t1_jejdt2x                1   
265  t1_jekledp         4.1.0.11   
272  t1_jejwjkb        4.1.1.0.2   
321  t1_jejogk9         4.4.0.12   
323  t1_jejqhux         4.4.0.14   
325  t1_jejr8ya         4.4.0.16   
350  t1_jejwmnl             4.16   
374  t1_jekaunx              5.8   
382  t1_jek20ro             5.16   
384  t1_jejg3jb             5.18   
385  t1_jejl16h             5.19   
398  t1_jel2zou             5.32   
404  t1_jenr03n             5.38   
406  t1_jespc4e             5.40   
419  t1_jejx06o             5.53   
421  t1_jem7rb4             5.55   
464  t1_jekhow9              9.4   
589  t1_jejnhpo               49   
610  t1_jej5yqz               69   
612  t1_jejd4it               71   
615  t1_jejfcg3               74   
619  t1_jejb0pl               78   
711  t1_jek7yu1              170   
745  t1_jekp1da              204   
830  t1_jeng7vk              289   
831  t1_jeng84j              290   

                                               comment  reply  score  
16                                           [deleted]   True     15  
21                                           [deleted]   True      1  
36                                           [deleted]   True      8  
67                                           [deleted]   True      1  
69                                           [deleted]   True      3  
71                                           [deleted]   True      8  
145                           I want to kiss your dad.   True      1  
146                     I'll believe it when I see it.   True    287  
265                                          [deleted]   True     -4  
272                           I want to kiss your dad.   True      8  
321                                          [deleted]   True      0  
323                                          [deleted]   True      0  
325                                          [deleted]   True      1  
350                           I want to kiss your dad.   True      2  
374                                          [deleted]   True      6  
382                                          [deleted]   True      5  
384                                          [deleted]   True     19  
385                                          [deleted]   True     -6  
398                                          [deleted]   True      3  
404                                          [deleted]   True      1  
406                                          [deleted]   True      1  
419                                          [deleted]   True     -1  
421                                          [deleted]   True      2  
464                                          [deleted]   True      3  
589                                              Good.  False      2  
610                                          [deleted]  False     19  
612                                          [deleted]  False      1  
615                                          [deleted]  False      2  
619                                          [deleted]  False      9  
711                                              Good.  False      1  
745                     I'll believe it when I see it.  False      1  
830  Don't own a house and probably never will be a...  False      1  
831  Don't own a house and probably never will be a...  False      1

In [30]:
dfCom = pd.DataFrame(all_data)
dfCom

name           thread  \
0    t1_jejbve6                0   
1    t1_jenxvwq  0.0.0.0.0.0.0.0   
2    t1_jemxr25  0.0.0.0.0.0.0.1   
3    t1_jel6f96    0.0.0.0.0.0.0   
4    t1_jenxm3e    0.0.0.0.0.0.1   
..          ...              ...   
897  t1_jeoazbd              356   
898  t1_jel3ujj              357   
899  t1_jel3zb2              358   
900  t1_jjqeyc8              359   
901  t1_jel69sb              360   

                                               comment  reply  score  
0    “There’s a housing shortage!”\n\n“There’s too ...   True    833  
1    If it has to have an LA address, what I found ...   True      4  
2                          And that’s if you’re lucky!   True      1  
3        And 400K might get you a tiny 1 bedroom condo   True     12  
4                         That's absolutely obnoxious.   True      2  
..                                                 ...    ...    ...  
897  I think it’s the moving back in with parents c...  False      1  
898  Jeez, come to the midwest. I’m just south of K...  False      1  
899                                       Yeah. Right.  False      1  
900                      Lol “lower rents”. Yeah right  False      1  
901  Not really. It might bring prices down and inv...  False      1  

[902 rows x 5 columns]

In [31]:
parent_id = "t3_128l6rd" #"t1_jel6f96" 
children_link = 'jemxr25' #''jekhmw2 jemxr25 jenxvwq
requestMore = requests.get(f"http://oauth.reddit.com/api/morechildren?link_id={parent_id}&children={children_link}&api_type=json", headers=headers)
requestMore = requestMore.json()
JSON(requestMore)

<IPython.core.display.JSON object>

In [32]:
# Subreddit posts
subreddit="StockMarket"
get_method="hot"
params={"limit":100,
        "g": "bf"
       }
request= requests.get(f"https://oauth.reddit.com/r/{subreddit}/{get_method}", headers=headers, params=params)
request= request.json()
JSON(request)

<IPython.core.display.JSON object>

In [33]:
# /search
params={
        "limit": 100,
        "q": "Taiwan"
       }
request= requests.get(f"https://oauth.reddit.com/search", headers=headers, params=params)
request= request.json()
JSON(request)

<IPython.core.display.JSON object>

In [34]:
# /best, hot, new
params={
        "limit": 100
       }
request= requests.get(f"https://oauth.reddit.com/hot", headers=headers, params=params)
request= request.json()
JSON(request)

<IPython.core.display.JSON object>

## Debugging session

In [35]:
params={"limit":100,
        "threaded":True,
        "sort":"new"
       }
request = requests.get('https://oauth.reddit.com/r/StockMarket/comments', headers=headers, params=params)
JSON(request.json())

<IPython.core.display.JSON object>

In [36]:
params={"limit":100,
        #"threaded":True,
        #"sort":"new"
       }
request = requests.get('https://oauth.reddit.com/morechildren', headers=headers, params=params)
JSON(request.json())

<IPython.core.display.JSON object>

In [37]:
#Post comments
linkId=all_data[5]
request = requests.get(f"https://oauth.reddit.com/comments/{linkId}", headers=headers)
JSON(request.json())

<IPython.core.display.JSON object>